# proglie

In [2]:
from sklearn import tree
from sklearn.ensemble import RandomForestClassifier
from sklearn import svm
from sklearn.naive_bayes import GaussianNB
from sklearn.model_selection import GridSearchCV
from sklearn.model_selection import cross_validate
from sklearn.model_selection import LeaveOneOut

import pandas as pd
import numpy as np
from statistics import mean

from IPython.core.interactiveshell import InteractiveShell
InteractiveShell.ast_node_interactivity = 'all'


# setting up labels for dataset
labels = ('class', 'spec_num', 'eccentr', 'asp_ratio', 'elong', 'solidity', 'stoch_conv', 'iso_factor',
          'max_ind_depth', 'lobedness', 'av_intensity', 'av_contr', 'smooth', 'third_mom', 'unif',
          'entropy')
# importing data
df = pd.read_csv(r'./leaf/leaf.csv', header = None, names = labels)

### random forest

we first use grid sarch with k-fold cross validation: for n_var we choose sqrt(p) and p/3, with p total number variable

In [4]:
k = 5   # number of folds

# building the grid
grid_param_rf = {'n_estimators': (100, 200, 500, 700),
                 'criterion': ('gini', 'entropy'),
                 'max_features': ('sqrt', 5)}

# shuffling the dataframe
df = df.sample(frac=1).reset_index()
df = df.iloc[:, 1:17]   # needed to eliminate the old indexes column
# separating y from x and eliminating specimen number variable
X = df.iloc[:, 2:16]
y = df.iloc[:, 0]

# grid search
rf_cv = GridSearchCV(RandomForestClassifier(), grid_param_rf, cv=k, scoring='balanced_accuracy', n_jobs=4)
rf_cv.fit(X, y)

GridSearchCV(cv=5, estimator=RandomForestClassifier(), n_jobs=4,
             param_grid={'criterion': ('gini', 'entropy'),
                         'max_features': ('sqrt', 5),
                         'n_estimators': (100, 200, 500, 700)},
             scoring='balanced_accuracy')

{'mean_fit_time': array([0.14077544, 0.24693475, 0.54734383, 0.74225597, 0.13063445,
       0.25021253, 0.60600929, 0.86253104, 0.14278502, 0.28396635,
       0.73212504, 1.01335874, 0.1806005 , 0.36510224, 0.8990047 ,
       1.23900247]), 'std_fit_time': array([0.02046005, 0.05417815, 0.06269723, 0.02750343, 0.00143268,
       0.00220357, 0.00515675, 0.02183589, 0.00189287, 0.00405309,
       0.01182307, 0.0420931 , 0.00488749, 0.01015855, 0.00508006,
       0.0343499 ]), 'mean_score_time': array([0.00869317, 0.01245856, 0.03094878, 0.04044528, 0.00695319,
       0.01244602, 0.02936597, 0.04132986, 0.00675507, 0.01238079,
       0.0302094 , 0.04036469, 0.00684457, 0.01214604, 0.02848845,
       0.04317393]), 'std_score_time': array([0.00191591, 0.00043847, 0.0027622 , 0.00076956, 0.00063276,
       0.00065388, 0.00114361, 0.00171559, 0.00011892, 0.00027266,
       0.00371446, 0.0013469 , 0.00032373, 0.00036913, 0.00060514,
       0.01114459]), 'param_criterion': masked_array(data=['gi

In [ ]:
# printing accuracy and best parameters

print(rf_cv.best_score_)
print(rf_cv.best_params_)

we now try with leave-one-out cross validation (pretty slow, but ok with less parameters)

In [ ]:
# building the grid
grid_param_rf_less = {'n_estimators': (100, 500),
                       'max_features': ('sqrt', 5)}

# shuffling the dataframe
df = df.sample(frac=1).reset_index()
df = df.iloc[:, 1:17]   # needed to eliminate the old indexes column
# separating y from x and eliminating specimen number variable
X = df.iloc[:, 2:16]
y = df.iloc[:, 0]

# grid search
rf_loocv = GridSearchCV(RandomForestClassifier(criterion='gini'), grid_param_rf_less, cv=LeaveOneOut(), scoring='accuracy', n_jobs=-2)
rf_loocv.fit(X, y)

In [ ]:
# printing accuracy and best parameters

print(rf_loocv.best_score_)
print(rf_loocv.best_params_)

### single tree

grid search with k-fold cross validation

In [ ]:
k = 5   # number of folds

# griglia dei parametri su cui fare la ricerca
grid_param_tree = {'criterion': ('gini', 'entropy'), 'min_samples_split': np.arange(2, 40)}

# shuffling the dataframe
df = df.sample(frac=1).reset_index()
df = df.iloc[:, 1:17]   # needed to eliminate the old indexes column
# separating y from x and eliminating specimen number variable
X = df.iloc[:, 2:16]
y = df.iloc[:, 0]

# grid search
tree_cv = GridSearchCV(tree.DecisionTreeClassifier(), grid_param_tree, cv=k, scoring='balanced_accuracy')
tree_cv.fit(X, y)

GridSearchCV(cv=5, estimator=DecisionTreeClassifier(),
             param_grid={'criterion': ('gini', 'entropy'),
                         'min_samples_split': array([ 2,  3,  4,  5,  6,  7,  8,  9, 10, 11, 12, 13, 14, 15, 16, 17, 18,
       19, 20, 21, 22, 23, 24, 25, 26, 27, 28, 29, 30, 31, 32, 33, 34, 35,
       36, 37, 38, 39])},
             scoring='balanced_accuracy')

In [ ]:
# printing accuracy and best parameters

print(tree_cv.best_score_)
print(tree_cv.best_params_)

0.6333333333333333
{'criterion': 'entropy', 'min_samples_split': 2}


grid search with leave-one-out cross validation

In [ ]:
# shuffling the dataframe
df = df.sample(frac=1).reset_index()
df = df.iloc[:, 1:17]   # needed to eliminate the old indexes column
# separating y from x and eliminating specimen number variable
X = df.iloc[:, 2:16]
y = df.iloc[:, 0]

# grid search
tree_loocv = GridSearchCV(tree.DecisionTreeClassifier(), grid_param_tree, cv=LeaveOneOut(), scoring='accuracy')
tree_loocv.fit(X, y)

In [ ]:
# printing accuracy and best parameters

print(tree_loocv.best_score_)
print(tree_loocv.best_params_)

### SVM

In [ ]:
# packages for pipelining and scaling

from sklearn.pipeline import Pipeline
from sklearn.preprocessing import StandardScaler
from sklearn.metrics import accuracy_score

grid search with k-fold cross validation: we use various kernels and a wide range for the C parameter; degree indicates the degree of the polynimial used in the kernel (if the kernel is not polynomial this parameter is ignored); decision_function_shape indicates the way in which the binary classifier technique is adapted to multiclass classification; gamma is a parameter used by some of the kernels (it is a rough measure of the distance of the significant data points)

before using the SVC classifier we performa a standard scaling on the input data

In [ ]:
# building the pipeline
pipe = Pipeline([('scaling', StandardScaler()),
                 ('SVM', svm.SVC(decision_function_shape='ovo'))])

k=5   # number of folds

# building the range of the regularization parameter (C) and of gamm
reg_param = np.logspace(-10, 11, 22)
gamm = np.logspace(-9, 3, 13)

grid_param_svm = {'SVM__C': reg_param,
                  'SVM__kernel': ('linear', 'poly', 'rbf', 'sigmoid'), 
                  'SVM__degree': np.arange(2, 5),
                  'SVM__decision_function_shape': ('ovo', 'ovr'),
                  'SVM__gamma': gamm}

# shuffling the dataframe
df = df.sample(frac=1).reset_index()
df = df.iloc[:, 1:17]   # needed to eliminate the old indexes column
# separating y from x and eliminating specimen number variable
X = df.iloc[:, 2:16]
y = df.iloc[:, 0]

# grid search
svm_cv = GridSearchCV(pipe, grid_param_svm, cv=k, scoring='balanced_accuracy', n_jobs=-2)
svm_cv.fit(X,y)

GridSearchCV(cv=5,
             estimator=Pipeline(steps=[('scaling', StandardScaler()),
                                       ('SVM',
                                        SVC(decision_function_shape='ovo'))]),
             n_jobs=-2,
             param_grid={'SVM__C': array([1.e-10, 1.e-09, 1.e-08, 1.e-07, 1.e-06, 1.e-05, 1.e-04, 1.e-03,
       1.e-02, 1.e-01, 1.e+00, 1.e+01, 1.e+02, 1.e+03, 1.e+04, 1.e+05,
       1.e+06, 1.e+07, 1.e+08, 1.e+09, 1.e+10, 1.e+11]),
                         'SVM__decision_function_shape': ('ovo', 'ovr'),
                         'SVM__degree': array([2, 3, 4]),
                         'SVM__gamma': array([1.e-09, 1.e-08, 1.e-07, 1.e-06, 1.e-05, 1.e-04, 1.e-03, 1.e-02,
       1.e-01, 1.e+00, 1.e+01, 1.e+02, 1.e+03]),
                         'SVM__kernel': ('linear', 'poly', 'rbf', 'sigmoid')},
             scoring='balanced_accuracy')

In [ ]:
# printing accuracy and best parameters

print(svm_cv.best_score_)
print(svm_cv.best_params_)

we now try with leave-one-out cross validation

In [ ]:
# shuffling the dataframe
df = df.sample(frac=1).reset_index()
df = df.iloc[:, 1:17]   # needed to eliminate the old indexes column
# separating y from x and eliminating specimen number variable
X = df.iloc[:, 2:16]
y = df.iloc[:, 0]

# grid search
svm_loocv = GridSearchCV(pipe, grid_param_svm, cv=LeaveOneOut(), scoring='accuracy', n_jobs=-2)
svm_loocv.fit(X,y)

In [ ]:
# printing accuracy and best parameters

print(svm_cv.best_score_)
print(svm_cv.best_params_)

VALUTARE SE METTERE ANCHE GRID SEARCH CON VALORI PIÙ SPECIFICI

### naive bayes

in this case we don't use grid search because we don't have any hyper-parameter to choose;
we use instead a k-fold cross validation and a leave-one-out cross validation to evaluate the technique

In [ ]:
k = 5

# shuffling the dataframe
#df = df.sample(frac=1).reset_index()
#df = df.iloc[:, 1:17]   # needed to eliminate the old indexes column
# separating y from x and eliminating specimen number variable
X = df.iloc[:, 2:16]
y = df.iloc[:, 0]

# k-fold cross validation
effect_NB_cv = cross_validate(GaussianNB(), X, y, cv=k, scoring='balanced_accuracy')

In [ ]:
# printing accuracy

print(mean(effect_NB_cv['test_score']))

0.7377777777777776


In [ ]:
# shuffling the dataframe
df = df.sample(frac=1).reset_index()
df = df.iloc[:, 1:17]   # needed to eliminate the old indexes column
# separating y from x and eliminating specimen number variable
X = df.iloc[:, 2:16]
y = df.iloc[:, 0]

# leave-one-out cross validation
effect_NB_loocv = cross_validate(GaussianNB(), X, y, cv=LeaveOneOut(), scoring='balanced_accuracy')

In [ ]:
# printing accuracy

print(mean(effect_NB_loocv['test_score']))

NameError: name 'mean' is not defined

### KNN with 5-fold CV

In [ ]:
from sklearn.neighbors import KNeighborsClassifier

rownum = df.shape[0] #number of rows of dataframe
k = 5
# griglia dei parametri su cui fare la ricerca
grid_param_cv = {   'n_neighbors': np.arange(1, rownum -rownum//k), 
                    'weights': ('uniform', 'distance'), 
                    'metric': ('cosine', 'euclidean', 'manhattan')
                }

# shuffling the dataframe
df = df.sample(frac=1).reset_index()
df = df.iloc[:, 1:17]   # needed to eliminate the old indexes column
# separating y from x and eliminating specimen number variable
X = df.iloc[:, 2:16]
y = df.iloc[:, 0]

knn_cv = GridSearchCV(  KNeighborsClassifier(), grid_param_cv, cv=k, scoring='balanced_accuracy', 
                        return_train_score=False, n_jobs =2, verbose=1)
knn_cv.fit(X, y)
print("Best scores after CV are: ", knn_cv.best_score_)
print("Best params after CV are: ", knn_cv.best_params_)

Fitting 5 folds for each of 1626 candidates, totalling 8130 fits


GridSearchCV(cv=5, estimator=KNeighborsClassifier(), n_jobs=2,
             param_grid={'metric': ('cosine', 'euclidean', 'manhattan'),
                         'n_neighbors': array([  1,   2,   3,   4,   5,   6,   7,   8,   9,  10,  11,  12,  13,
        14,  15,  16,  17,  18,  19,  20,  21,  22,  23,  24,  25,  26,
        27,  28,  29,  30,  31,  32,  33,  34,  35,  36,  37,  38,  39,
        40,  41,  42,  43,  44,  45,  46,  47,  48,  49,  50,  51,  52,
        53,  54,  55,  56,  57,  58,  59,  60,  61,  62,  63,  64,  65,
        66,  67,  68,  69,  70,  71,  72,  73,  74,...
       196, 197, 198, 199, 200, 201, 202, 203, 204, 205, 206, 207, 208,
       209, 210, 211, 212, 213, 214, 215, 216, 217, 218, 219, 220, 221,
       222, 223, 224, 225, 226, 227, 228, 229, 230, 231, 232, 233, 234,
       235, 236, 237, 238, 239, 240, 241, 242, 243, 244, 245, 246, 247,
       248, 249, 250, 251, 252, 253, 254, 255, 256, 257, 258, 259, 260,
       261, 262, 263, 264, 265, 266, 267, 268, 269, 270, 271]),
                         'weights': ('uniform', 'distance')},
             scoring='balanced_accuracy', verbose=1)

Best scores after CV are:  0.6699999999999999
Best params after CV are:  {'metric': 'manhattan', 'n_neighbors': 4, 'weights': 'distance'}


### KNN with LOOCV

In [ ]:
from sklearn.neighbors import KNeighborsClassifier

# griglia dei parametri su cui fare la ricerca. Per quanto riguarda n_neighbours come mai abbiamo scelto quel range?
grid_param_less = { 'n_neighbors': np.arange(1, 30), 
                    'weights': ('uniform', 'distance'),
                    'metric': ('cosine', 'euclidean', 'manhattan')}
# shuffling the dataframe
df = df.sample(frac=1).reset_index()
df = df.iloc[:, 1:17]   # needed to eliminate the old indexes column
df.shape
# separating y from x and eliminating specimen number variable
X = df.iloc[:, 2:16]
y = df.iloc[:, 0]

knn_loocv = GridSearchCV(KNeighborsClassifier(), grid_param_less, cv=LeaveOneOut(), scoring='balanced_accuracy', return_train_score=False, n_jobs=-2)
knn_loocv.fit(X, y)
print("Best scores after LOOCV are: ", knn_loocv.best_score_)
print("Best params after LOOCV are: ", knn_loocv.best_params_)

(340, 16)

/home/pettepiero/.local/lib/python3.10/site-packages/sklearn/metrics/_classification.py:2184: UserWarning: y_pred contains classes not in y_true
  warnings.warn("y_pred contains classes not in y_true")
/home/pettepiero/.local/lib/python3.10/site-packages/sklearn/metrics/_classification.py:2184: UserWarning: y_pred contains classes not in y_true
  warnings.warn("y_pred contains classes not in y_true")
/home/pettepiero/.local/lib/python3.10/site-packages/sklearn/metrics/_classification.py:2184: UserWarning: y_pred contains classes not in y_true
  warnings.warn("y_pred contains classes not in y_true")
/home/pettepiero/.local/lib/python3.10/site-packages/sklearn/metrics/_classification.py:2184: UserWarning: y_pred contains classes not in y_true
  warnings.warn("y_pred contains classes not in y_true")
/home/pettepiero/.local/lib/python3.10/site-packages/sklearn/metrics/_classification.py:2184: UserWarning: y_pred contains classes not in y_true
  warnings.warn("y_pred contains classes not in

GridSearchCV(cv=LeaveOneOut(), estimator=KNeighborsClassifier(), n_jobs=-2,
             param_grid={'metric': ('cosine', 'euclidean', 'manhattan'),
                         'n_neighbors': array([ 1,  2,  3,  4,  5,  6,  7,  8,  9, 10, 11, 12, 13, 14, 15, 16, 17,
       18, 19, 20, 21, 22, 23, 24, 25, 26, 27, 28, 29]),
                         'weights': ('uniform', 'distance')},
             scoring='balanced_accuracy')

Best scores after LOOCV are:  0.6823529411764706
Best params after LOOCV are:  {'metric': 'manhattan', 'n_neighbors': 4, 'weights': 'distance'}
